In [ ]:
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth
else:
    # Do this only in Colab notebooks! Otherwise use pip install unsloth
    !pip install --no-deps bitsandbytes accelerate xformers==0.0.29.post3 peft trl==0.15.2 triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf datasets huggingface_hub hf_transfer
    !pip install --no-deps unsloth

In [ ]:
!pip install unsloth

In [ ]:
import pickle
file_path = 'mathdial_sft.pkl'

In [ ]:
with open(file_path, 'rb') as file:
    data = pickle.load(file)

# Now `data` holds whatever was stored — dict, list, model, etc.
print(type(data))

<class 'pandas.core.frame.DataFrame'>


In [ ]:
print(data.head())

                                         instruction  \
0  <Instructions>\nYou’re a math tutor. Each turn...   
1  <Instructions>\nYou’re a math tutor. Each turn...   
2  <Instructions>\nYou’re a math tutor. Each turn...   
3  <Instructions>\nYou’re a math tutor. Each turn...   
4  <Instructions>\nYou’re a math tutor. Each turn...   

                                               input  \
0  {"student_persona": {"name": "Ayisha", "gender...   
1  {"student_persona": {"name": "Ayisha", "gender...   
2  {"student_persona": {"name": "Ayisha", "gender...   
3  {"student_persona": {"name": "Ayisha", "gender...   
4  {"student_persona": {"name": "Rishi", "gender"...   

                                              output  
0  Hi Ayisha, I noticed you were using months in ...  
1  Great start! Now, how many servings are in the...  
2  Exactly! Now, how many nights will those 96 se...  
3  That's right, Ayisha! You solved it perfectly....  
4  Hi Rishi, it looks pretty good but let's focus..

In [ ]:
import pandas as pd

pd.set_option('display.max_rows', None)       # Show all rows
pd.set_option('display.max_columns', None)    # Show all columns
pd.set_option('display.width', 0)             # Auto-detect width
pd.set_option('display.max_colwidth', None)

In [ ]:
import pandas as pd

df = pd.read_pickle("mathdial_sft.pkl")  # Load with original env

In [ ]:
print(df.head())

In [ ]:
import pandas as pd


# Save first n rows to a CSV
n = 5  # You can change this to however many rows you want
df_5 = df.head(n)
# df_5.to_csv("dataset_head.csv", index=False)

# print("Saved first", n, "rows to 'dataset_head.csv'")

In [ ]:
print(df_5)

In [ ]:
df_5["output"]

0    Hi Ayisha, I noticed you were using months in your calculations. Let's try to focus just on the nights. Can you think of it like a puzzle? How many nights will the honey last without considering months?
1                                                                                                                                                    Great start! Now, how many servings are in the entire jar?
2                                                                                                                   Exactly! Now, how many nights will those 96 servings last if she uses 2 servings per night?
3                                                                                That's right, Ayisha! You solved it perfectly. It's just like solving a logic puzzle—focus on the relevant details. Well done!
4                                                                  Hi Rishi, it looks pretty good but let's focus on your third step. We know Jame tears 30 cards at a time, right? So recheck your third step.
Name: output, dtype: object

In [ ]:
jsonl_path = 'mathdial.json'
import json

with open(jsonl_path, "w") as f:
    for idx, row in df.iterrows():
        # Parse the 'input' column which contains nested JSON as a string
        output = row["output"]
        parsed_input = json.loads(row["input"])
        # print(parsed_input)
        instruction_text = (
        "You are a math tutor. Each turn you get these inputs: student persona and conversation history. "
        "Your goal is to guide the student using Socratic questions based on their thinking. "
        "Never give the final answer.")

        # Extract student persona and conversation history
        persona = parsed_input["student_persona"]
        history = parsed_input["conversation_history"]
        # instruction_text = parsed_input["instruction"]

        # Add teacher's next turn from 'output' column
        teacher_turn = {"speaker": "teacher", "text": row["output"]}
        full_conversation = history + [teacher_turn]

        # Construct the final training record
        training_example = {
            "instruction": instruction_text,
            "persona": persona,
            "conversation": full_conversation,
            "output" : output
        }
        print(training_example)
        f.write(json.dumps(training_example) + "\n")

Streaming output truncated to the last 5000 lines.
{'instruction': 'You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.', 'persona': {'name': 'Seth', 'gender': 'male', 'interests': 'programming, puzzles, logic games', 'personality': 'curious, precise, enjoys deep thinking', 'background': "often gets absorbed in long-term projects; loves asking 'why' and breaking problems into patterns and rules."}, 'conversation': [{'speaker': 'teacher', 'text': 'Hello Seth, can you talk me through your solution?'}, {'speaker': 'student', 'text': 'Sure. I said that the rival team won twice as many matches as the home team, so they won 2 x 3 = 6 matches. Both teams won 3 matches each, and the rival team won an additional 6 matches, so they won a total of 3 + 6 = 9 matches. Both teams drew 4 matches each, so together they drew a total of 4 + 4 = 8 ma

In [ ]:
!pip install -q datasets transformers accelerate


In [ ]:
import json
from sklearn.model_selection import train_test_split

with open("mathdial.json", "r") as f:
    raw_data = [json.loads(line) for line in f]

train_data, test_data = train_test_split(raw_data, test_size=0.1, random_state=42)

# print(f"Train: {len(train_data)}, Validation: {len(val_data)}, Test: {len(test_data)}")


In [ ]:
from huggingface_hub import login
login(token="Hugging_face_token")

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

In [ ]:
# Format + tokenize with teacher masking
def format_example(example):
    persona = example["persona"]
    persona_text = f"Student Persona: {persona['name']}, {persona['gender']}, interests: {persona['interests']}, " \
                   f"personality: {persona['personality']}, background: {persona['background']}\n"

    dialogue = example["conversation"]
    full_text = example["instruction"] + "\n" + persona_text + "\n"

    current_pos = len(tokenizer(full_text, return_tensors="pt").input_ids[0])
    mask_positions = []

    for turn in dialogue:
        turn_text = f"{turn['speaker'].capitalize()}: {turn['text']}\n"
        tokens = tokenizer(turn_text, return_tensors="pt", add_special_tokens=False).input_ids[0]
        if turn['speaker'] == "teacher":
            mask_positions.extend(range(current_pos, current_pos + len(tokens)))
        current_pos += len(tokens)
        full_text += turn_text

    tokenized = tokenizer(full_text, return_tensors="pt", padding="max_length", truncation=True, max_length=512)
    input_ids = tokenized.input_ids[0]
    attention_mask = tokenized.attention_mask[0]
    labels = input_ids.clone()

    for i in range(len(labels)):
        if i not in mask_positions:
            labels[i] = -100

    return {
        "input_ids": input_ids,
        "attention_mask": attention_mask,
        "labels": labels
    }

In [ ]:
from datasets import Dataset, DatasetDict

def make_text(example):
    # 1. Instruction
    instruction = example["instruction"]
    # 2. Persona
    p = example["persona"]
    persona_block = (
        f"Student Persona: {p['name']}, {p['gender']}, interests: {p['interests']}, "
        f"personality: {p['personality']}, background: {p['background']}"
    )
    # 3. Conversation history
    history = ""
    for turn in example["conversation"]:
        history += f"{turn['speaker'].capitalize()}: {turn['text']}\n"
    # 4. Gold teacher output
    teacher_out = example["output"]
    # 5. Assemble full text
    full = (
        f"{instruction}\n"
        f"{persona_block}\n\n"
        f"{history}"
    )
    return {"text": full}

# Suppose raw_train and raw_val are lists of your dict examples
ds_train = Dataset.from_list(train_data).map(make_text, remove_columns=train_data[0].keys())
# ds_val   = Dataset.from_list(raw_val).map(make_text,   remove_columns=raw_val[0].keys())

dataset = DatasetDict({
    "train": ds_train,
    # "val":   ds_val
})


Map:   0%|          | 0/12081 [00:00<?, ? examples/s]

In [ ]:
train_data[0].keys()

dict_keys(['instruction', 'persona', 'conversation', 'output'])

In [ ]:
pip install bitsandbytes

In [ ]:
from unsloth import FastLanguageModel
import torch

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True  # Use 4bit quantization to reduce memory usage. Can be False.

# 4bit pre quantized models we support for 4x faster downloading + no OOMs.
fourbit_models = [
    "unsloth/mistral-7b-v0.3-bnb-4bit",  # New Mistral v3 2x faster!
    "unsloth/mistral-7b-instruct-v0.3-bnb-4bit",
    "unsloth/llama-3-8b-bnb-4bit",  # Llama-3 15 trillion tokens model 2x faster!
    "unsloth/llama-3-8b-Instruct-bnb-4bit",
    "unsloth/llama-3-70b-bnb-4bit",
    "unsloth/Phi-3-mini-4k-instruct",  # Phi-3 2x faster!
    "unsloth/Phi-3-medium-4k-instruct",
    "unsloth/mistral-7b-bnb-4bit",
    "unsloth/gemma-7b-bnb-4bit",  # Gemma 2.2x faster!
]  # More models at https://huggingface.co/unsloth

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name="unsloth/llama-3-8b-bnb-4bit",
    max_seq_length=max_seq_length,
    dtype=dtype,
    load_in_4bit=load_in_4bit,
    # token = "hf_...", # use one if using gated models like meta-llama/Llama-2-7b-hf
)

==((====))==  Unsloth 2025.4.7: Fast Llama patching. Transformers: 4.51.3.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


model.safetensors:   0%|          | 0.00/5.70G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/198 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/50.6k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

In [ ]:
from datasets import Dataset, DatasetDict

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token

train_tokenized = [format_example(ex) for ex in train_data]

dataset = DatasetDict({
    "train": Dataset.from_list(train_tokenized)
})

In [ ]:
model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth 2025.4.7 patched 32 layers with 32 QKV layers, 32 O layers and 32 MLP layers.


In [ ]:
from trl import SFTTrainer
from transformers import TrainingArguments
from unsloth import is_bfloat16_supported

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset["train"],
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    dataset_num_proc = 2,
    packing = False, # Can make training 5x faster for short sequences.
    args = TrainingArguments(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        max_steps = 60,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "outputs",
    ),
)

Unsloth: Tokenizing ["text"] (num_proc=2):   0%|          | 0/12081 [00:00<?, ? examples/s]

In [ ]:
dataset["train"][0]

{'text': "You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.\nStudent Persona: Jordy, male, interests: programming, puzzles, logic games, personality: curious, precise, enjoys deep thinking, background: often gets absorbed in long-term projects; loves asking 'why' and breaking problems into patterns and rules.\n\nTeacher: Hi Jordy. I know you love puzzles and logic games, so let's break this problem down step by step. Have you read the question carefully? Can you go through the question with me?\nStudent: Hi! Yes, I read the question carefully. The question is asking how many kitchens are there on the entire space station. To solve this, I first figured out that each cylindrical structure has 12 + 7 + x = 19 + x rooms, where x is the number of kitchens. Then, since there are three cylindrical structures, the total number of rooms 

In [ ]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 12,081 | Num Epochs = 1 | Total steps = 60
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 4 x 1) = 8
 "-____-"     Trainable parameters = 41,943,040/8,000,000,000 (0.52% trained)


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize?ref=models
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: suvidsahay (suvidsahay-university-of-massachusetts-amherst) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


Unsloth: Will smartly offload gradients to save VRAM!


TrainOutput(global_step=60, training_loss=0.8962791264057159, metrics={'train_runtime': 769.8592, 'train_samples_per_second': 0.623, 'train_steps_per_second': 0.078, 'total_flos': 1.1010849804337152e+16, 'train_loss': 0.8962791264057159})

In [ ]:
# alpaca_prompt = Copied from above
FastLanguageModel.for_inference(model) # Enable native 2x faster inference

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(128256, 4096, padding_idx=128255)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Identity()
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_proj): lor

In [ ]:
def build_pace_prompt(instruction, persona, history):
    # Format the student persona section
    persona_text = f"Student Persona: {persona['name']}, {persona['gender']}, " \
                   f"interests: {persona['interests']}, personality: {persona['personality']}, " \
                   f"background: {persona['background']}"

    # Format the conversation history
    history_text = ""
    for turn in history:
        history_text += f"{turn['speaker'].capitalize()}: {turn['text']}\n"

    # Combine everything into a single prompt
    return f"{instruction}\n{persona_text}\n\n{history_text}Teacher:"

In [ ]:
save_dir = "pace_model_final"  # or any output folder you prefer

# Save model weights
model.save_pretrained(save_dir)

# Save tokenizer (vocab, merges, config)
tokenizer.save_pretrained(save_dir)

('pace_model_final/tokenizer_config.json',
 'pace_model_final/special_tokens_map.json',
 'pace_model_final/tokenizer.json')

In [ ]:
trainer.save_model("/content/drive/MyDrive/PACE/v1")

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
test_data[0]

In [ ]:
import torch
from tqdm import tqdm

def build_pace_prompt(instruction, persona, history):
    # 1) If the last turn is from the teacher, drop it:
    clean_history = history.copy()
    if clean_history and clean_history[-1]["speaker"] == "teacher":
        clean_history = clean_history[:-1]

    # 2) Build the persona block
    persona_text = (
        f"Student Persona: {persona['name']}, {persona['gender']}, "
        f"interests: {persona['interests']}, personality: {persona['personality']}, "
        f"background: {persona['background']}"
    )

    # 3) Build the (filtered) history text
    history_text = ""
    for turn in clean_history:
        history_text += f"{turn['speaker'].capitalize()}: {turn['text']}\n"

    # 4) Return prompt ending in "Teacher:" for generation
    return f"{instruction}\n{persona_text}\n\n{history_text}Teacher:"


def generate_teacher_responses_batch(model, tokenizer, test_data, batch_size=4, max_new_tokens=80):
    model.eval()
    results = []

    for i in tqdm(range(0, len(test_data), batch_size)):
        batch = test_data[i:i+batch_size]
        prompts = [build_pace_prompt(ex["instruction"], ex["persona"], ex["conversation"]) for ex in batch]

        # Tokenize as a batch
        inputs = tokenizer(prompts, return_tensors="pt", padding=True, truncation=True).to(model.device)

        # Generate
        with torch.no_grad():
            output_ids = model.generate(
                input_ids=inputs["input_ids"],
                attention_mask=inputs["attention_mask"],
                max_new_tokens=max_new_tokens,
                temperature=0.7,
                top_p=0.9,
                pad_token_id=tokenizer.eos_token_id
            )

        # Decode and extract response
        generated_texts = tokenizer.batch_decode(output_ids, skip_special_tokens=True)
        for j, full_output in enumerate(generated_texts):
            original_prompt = prompts[j]
            response = full_output[len(original_prompt):].strip()

            print(f"OG prompt:{j}", original_prompt)
            print(f"Generated response:{j}", response)

            results.append({
                "instruction": batch[j]["instruction"],
                "persona": batch[j]["persona"],
                "history": batch[j]["conversation"],
                "predicted_teacher_response": response
            })

    return results


In [ ]:
res = generate_teacher_responses_batch(model, tokenizer, test_data)

 33%|███▎      | 1/3 [00:25<00:50, 25.09s/it]

OG prompt:0 You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.
Student Persona: Winnie, male, interests: skateboarding, fixing bikes, DIY videos, personality: active, mechanical-minded, improvisational, background: prefers learning by doing and experimenting; gets easily bored by lectures but loves building and solving real-world problems.

Teacher: Hi Winnie, can you explain your answer?
Student: Sure. I used the information given in the problem to calculate that 25% of the people Aimee polled were women who opposed the idea. Then, I set up an equation to solve for x, which is the total number of people she polled. 0.25x = 39, so x = 39/0.25, which is equal to 156.
Teacher:
Generated response:0 :;hizmet:; thejspx:; 25:; and thejspx: 26:; and thejspx: 2lbrace:; and thejspx: 3jspx:; and thejspx: 4jspx:; and thejspx: 5jspx:; and the

 67%|██████▋   | 2/3 [00:50<00:25, 25.13s/it]

OG prompt:0 You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.
Student Persona: Mariana, female, interests: programming, puzzles, logic games, personality: curious, precise, enjoys deep thinking, background: often gets absorbed in long-term projects; loves asking 'why' and breaking problems into patterns and rules.

Teacher: Mariana, let's go over the problem again. How often does Janet use 15 pounds of cat litter?
Student: Janet uses 15 pounds of cat litter weekly.
Teacher: Great! Now, how many weeks does she need to buy for if she wants to cover 210 days?
Student: She needs to buy enough cat litter to last for 210/7 = 30 weeks.
Teacher: Exactly, and how many pounds of litter does she need in total for those 30 weeks?
Student: She needs a total of 105 x 30 = 3150 pounds of cat litter.
Teacher: Let's pause there. You mentioned 105

100%|██████████| 3/3 [01:10<00:00, 23.48s/it]

OG prompt:0 You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.
Student Persona: Alejandra, female, interests: programming, puzzles, logic games, personality: curious, precise, enjoys deep thinking, background: often gets absorbed in long-term projects; loves asking 'why' and breaking problems into patterns and rules.

Teacher:
Generated response:0 like thejspx:lbrace in thejspx: to awcharuis; and to awhilq: to awhilx: to awhil; and to awhil: to awcharuis; and to awhil: to awicklung: to awicklung: to awicklung: to a:zbollah: to a:zbollah: to a:zbollah: to a:zbollah
OG prompt:1 You are a math tutor. Each turn you get these inputs: student persona and conversation history. Your goal is to guide the student using Socratic questions based on their thinking. Never give the final answer.
Student Persona: Brenda, female, interests: progra

In [ ]:
teacher_responses = [r["predicted_teacher_response"] for r in res]


In [ ]:
test_data[0].keys()

dict_keys(['instruction', 'persona', 'conversation', 'output'])

In [ ]:
!pip install evaluate sacrebleu rouge_score


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.8/51.8 kB 4.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.1/104.1 kB 10.6 MB/s eta 0:00:00
  Created wheel for rouge_score: filename=rouge_score-0.1.2-py3-none-any.whl size=24934 sha256=ad7890513e11307de1a5aaa4ef4fdac8c4b5800089493d3d90e1aab0806eaab5
  Stored in directory: /root/.cache/pip/wheels/1e/19/43/8a442dc83660ca25e163e1bd1f89919284ab0d0c1475475148
Successfully built rouge_score


In [ ]:
num_preds = len(teacher_responses)

predictions = teacher_responses
references  = [ex["output"] for ex in test_data[:num_preds]]

In [ ]:
references

["I see where you're coming from, but let's think of it like fixing a bike. If 65% of the women are opposed and that number is 39, how do we find the total number of women, like figuring out the total parts of a bike when you know how many are broken?",
 "Exactly! It's the difference between the total bill and the pre-gratuity amount. Remember, it's not about percentages here, but the actual difference.",
 "Alright Hunter, let's tackle this problem step by step, just like strategizing for a soccer game.",
 'If 70% of your friends are female, then 30% are male. The number of male friends is already given, which is 15. So 30/100 * X = 15, and X = 50, where X is the total number of friends. Now, if we figured the total number of friends is 50 and 15 are males, then 50 - 15 = 35 are females.',
 "That's right! Now, how many 45-pound containers would she need for 450 pounds?",
 "Perfect! Now, let's combine the red and black socks. How many pairs do we have now?",
 'Great! Now add this to the

In [ ]:
teacher_responses

[':;hizmet:; thejspx:; 25:; and thejspx: 26:; and thejspx: 2lbrace:; and thejspx: 3jspx:; and thejspx: 4jspx:; and thejspx: 5jspx:; and thejspx: 6:; and thejspx: 7:; and thejspx: 8',
 ": I'm sorry, I don't know the answer.\n.swing: I'm sorry, I don't know the answer.\nTeacher: тва: I'm sorry, I don't know the answer.\nTeacher: тва: I'm sorry, I don't know the answer.\nTeacher: тва: I'm sorry, I don't know the answer.\nTeacher: тва: I'm sorry, I don",
 ',.flinklbrace:wl:lbrace:flix:flix:flix:flix:flix:flix:flix:flix:flix:flix:flix:jspx:flix:flix:jspx:jspx:jspx:jspx:flix:jspx:flix:flix:flix:flix:jspx:flix:;q:flix:;t:;f:;;h;;e:;;',
 'What if we had 100 friends and 70% of them were female, how many male friends would we have?\nStudent: If we had 100 friends and 70% of them were female, then we would have 30% of 100 friends, which is 30 male friends.\nTeacher: How many female friends would we have then?\nTeacher: How many female friends would we have',
 ':jspx:jspx:;0:flix:;0:;0:;0:;0:;0:;0

In [ ]:
import evaluate
bleu = evaluate.load("bleu")
rouge = evaluate.load("rouge")

bleu_res = bleu.compute(predictions=teacher_responses, references=references)

rouge_res = rouge.compute(
    predictions=teacher_responses,
    references=references,
    use_stemmer=True
)

In [ ]:
print("BLEU:", bleu_res["bleu"])
print("ROUGE-1:", rouge_res["rouge1"])
print("ROUGE-2:", rouge_res["rouge2"])
print("ROUGE-L:", rouge_res["rougeL"])

BLEU: 0.011699997816019313
ROUGE-1: 0.0935978835978836
ROUGE-2: 0.01698521456905878
ROUGE-L: 0.06929453262786597
